In [1]:
# Hier werden alle verwendeten Pythonmodule importiert
import Datenbank
import Import
import importlib
import Koordinatentransformationen
import sqlite3
import Funktionales_Modell
import Berechnungen
import Parameterschaetzung
import Stochastisches_Modell
from Stochastisches_Modell import StochastischesModell
import Export
import Netzqualität_Genauigkeit

In [2]:
importlib.reload(Datenbank)
importlib.reload(Import)
# Anlegen der Datenbank, wenn nicht vorhanden
pfad_datenbank = r"Campusnetz.db"
Datenbank.Datenbank_anlegen(pfad_datenbank)

# Import vervollständigen
imp = Import.Import(pfad_datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

In [3]:
# Import der Koordinatendatei(en) vom Tachymeter
pfad_datei = r"Daten\campsnetz_koordinaten_bereinigt.csv"
imp.import_koordinaten_lh_tachymeter(pfad_datei)

Der Import der Näherungskoordinaten wurde erfolgreich abgeschlossen


In [4]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
# Transformationen in ETRS89 / DREF91 Realisierung 2025
print(db_zugriff.get_koordinaten("naeherung_lh"))

{'10009': Matrix([
[1000.0],
[2000.0],
[ 100.0]]), '10006': Matrix([
[   1000.0],
[2032.6863],
[  99.5825]]), '10010': Matrix([
[1011.8143],
[1973.3252],
[  99.9259]]), '10018': Matrix([
[1008.5759],
[ 1942.762],
[ 100.2553]]), '10008': Matrix([
[979.7022],
[1991.401],
[  99.732]]), '10005': Matrix([
[ 966.5154],
[2014.6496],
[    99.72]]), '10003': Matrix([
[ 908.4312],
[1996.1248],
[  99.7403]]), '10004': Matrix([
[ 954.1536],
[2021.6822],
[  99.4916]]), '10007': Matrix([
[ 921.7481],
[1973.6201],
[  99.9176]]), '10001': Matrix([
[ 833.9439],
[1978.3737],
[  99.8946]]), '10002': Matrix([
[ 875.9684],
[1998.5174],
[  99.5867]]), '10016': Matrix([
[ 928.2783],
[1944.0082],
[ 100.0459]]), '10011': Matrix([
[844.9567],
[1891.157],
[ 99.8117]]), '10026': Matrix([
[1020.0059],
[1913.8703],
[ 100.3059]]), '10027': Matrix([
[1016.9451],
[1866.2914],
[ 100.3251]]), '10043': Matrix([
[1031.2077],
[1822.4739],
[ 100.3035]]), '10044': Matrix([
[ 1025.976],
[1782.4835],
[ 100.5461]]), '10021': Ma

In [5]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
# Transformationen in ETRS89 / DREF91 Realisierung 2025
print(db_zugriff.get_koordinaten("naeherung_us"))

{}


In [28]:
importlib.reload(Import)
imp = Import.Import(pfad_datenbank)

pfad_koordinaten_gnss = r"Daten\Koordinaten_OL_umliegend_bereinigt.csv"
# X, Y, Z der SAPOS-Stationen
genauigkeit_sapos_referenzstationen = [0.05, 0.04, 0.09]

imp.import_koordinaten_gnss(pfad_koordinaten_gnss, genauigkeit_sapos_referenzstationen)


'Import der Koordinaten aus stationärem GNSS abgeschlossen.'

In [29]:
# ToDo: Sobald GNSS vorliegend Koordinaten im ETRS89 / DREF 91 (2025) daraus berechnen!
#liste_koordinaten_naeherung_us = {
#    10001: (3794874.984, 546741.752, 5080029.990),
#    10002: (3794842.533, 546726.907, 5080071.133),
#    10037: (3794774.148, 546955.423, 5080040.520),
#    10044: (3794725.786, 546954.557, 5080084.411),
#}


#con = sqlite3.connect(pfad_datenbank)
#cursor = con.cursor()
#sql = """
#UPDATE Netzpunkte
#SET naeherungx_us = ?, naeherungy_us = ?, naeherungz_us = ?
#WHERE punktnummer = ?
#"""
#for punktnummer, (x, y, z) in #liste_koordinaten_naeherung_us.items():
#    cursor.execute(sql, (x, y, z, punktnummer))
#con.commit()
#cursor.close()
#con.close()

In [30]:
# ToDo: Sobald GNSS-Daten vorliegen und die Berechnungen richtig sind, aufräumen!!!

importlib.reload(Koordinatentransformationen)
trafos = Koordinatentransformationen.Transformationen(pfad_datenbank)


import numpy as np

import itertools
import numpy as np
import sympy as sp

db = Datenbank.Datenbankzugriff(pfad_datenbank)
dict_ausgangssystem = db.get_koordinaten("naeherung_lh", "Dict")
dict_zielsystem = db.get_koordinaten("naeherung_us", "Dict")

gemeinsame_punktnummern = sorted(set(dict_ausgangssystem.keys()) & set(dict_zielsystem.keys()))
anzahl_gemeinsame_punkte = len(gemeinsame_punktnummern)

liste_punkte_ausgangssystem = [dict_ausgangssystem[i] for i in gemeinsame_punktnummern]
liste_punkte_zielsystem = [dict_zielsystem[i] for i in gemeinsame_punktnummern]

def dist(a, b):
    return float((a - b).norm())

print("d(p2,p1)=", dist(liste_punkte_ausgangssystem[1], liste_punkte_ausgangssystem[0]))
print("d(P2,P1)=", dist(liste_punkte_zielsystem[1], liste_punkte_zielsystem[0]))
print("m0 ~", dist(liste_punkte_zielsystem[1], liste_punkte_zielsystem[0]) /
               dist(liste_punkte_ausgangssystem[1], liste_punkte_ausgangssystem[0]))


def dist(a, b):
    return float((a - b).norm())

ratios = []
pairs = list(itertools.combinations(range(len(liste_punkte_ausgangssystem)), 2))

for i, j in pairs:
    d_loc = dist(liste_punkte_ausgangssystem[i], liste_punkte_ausgangssystem[j])
    d_ecef = dist(liste_punkte_zielsystem[i], liste_punkte_zielsystem[j])
    if d_loc > 1e-6:
        ratios.append(d_ecef / d_loc)

print("Anzahl Ratios:", len(ratios))
print("min/mean/max:", min(ratios), sum(ratios)/len(ratios), max(ratios))
print("std:", float(np.std(ratios)))

S_loc = sum(liste_punkte_ausgangssystem, sp.Matrix([0,0,0])) / anzahl_gemeinsame_punkte
S_ecef = sum(liste_punkte_zielsystem, sp.Matrix([0,0,0])) / anzahl_gemeinsame_punkte

print("S_loc:", S_loc)
print("S_ecef:", S_ecef)
print("Delta:", (S_ecef - S_loc).evalf(6))


def dist(a, b):
    return float((a - b).norm())

n = len(liste_punkte_ausgangssystem)

scores = []
for i in range(n):
    d_loc = []
    d_ecef = []
    for j in range(n):
        if i == j:
            continue
        d_loc.append(dist(liste_punkte_ausgangssystem[i], liste_punkte_ausgangssystem[j]))
        d_ecef.append(dist(liste_punkte_zielsystem[i], liste_punkte_zielsystem[j]))

    d_loc = np.array(d_loc)
    d_ecef = np.array(d_ecef)

    # Verhältnisvektor; robust gegen Nullschutz
    r = d_ecef / np.where(d_loc == 0, np.nan, d_loc)

    # Streuung der Ratios für Punkt i
    score = np.nanstd(r)
    scores.append(score)

for pn, sc in sorted(zip(gemeinsame_punktnummern, scores), key=lambda x: -x[1]):
    print(pn, round(sc, 4))



transformationsparameter = trafos.Helmerttransformation_Euler_Transformationsparameter_berechne()

d(p2,p1)= 46.60388451996242
d(P2,P1)= 46.59145296840883
m0 ~ 0.999733250743331
Anzahl Ratios: 45
min/mean/max: 0.9986498495467658 0.9999468893556359 1.0004164038548047
std: 0.00025301851725699595
S_loc: Matrix([[937.945990000000], [1847.25831000000], [99.9451600000000]])
S_ecef: Matrix([[3794821.39483000], [546885.587320000], [5080110.27740000]])
Delta: Matrix([[3.79388e+6], [545038.], [5.08001e+6]])
10054 0.0004
10059 0.0004
10037 0.0002
10028 0.0002
10044 0.0001
10001 0.0001
10014 0.0001
10002 0.0001
10026 0.0001
10008 0.0001
Anzahl gemeinsame Punkte: 10

Erste Zielpunkte:
10001 [3794901.5252, 546745.559, 5080065.7672]
10002 [3794866.9711, 546729.5958, 5080092.6364]
10008 [3794783.8581, 546746.6347, 5080152.7404]
10014 [3794838.7464, 546812.3658, 5080105.2]
10026 [3794753.8595, 546827.4296, 5080167.0938]

Erste Ausgangspunkte:
10001 [833.9439, 1978.3737, 99.8946]
10002 [875.9684, 1998.5174, 99.5867]
10008 [979.7022, 1991.401, 99.732]
10014 [913.9706, 1918.7731, 99.8872]
10026 [1020.0

In [ ]:
importlib.reload(Koordinatentransformationen)
trafos = Koordinatentransformationen.Transformationen(pfad_datenbank)

koordinaten_transformiert = trafos.Helmerttransformation(transformationsparameter)
print(koordinaten_transformiert)

In [ ]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

db_zugriff.set_koordinaten(koordinaten_transformiert, "naeherung_us")

In [ ]:
# Importieren der tachymetrischen Beobachtungen
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

db_zugriff.get_instrument_liste("Tachymeter")
db_zugriff.set_instrument("Tachymeter", "Trimble S9")
db_zugriff.get_instrument_liste("Tachymeter")

In [ ]:
#Importieren der apriori Genauigkeitsinformationen
#Zulässige Beobachtungsarten = "Tachymeter_Richtung", "Tachymeter_Strecke"
# Wenn Beobachtungsart = "Tachymeter_Richtung" --> Übergabe in Milligon und nur Stabw_apriori_konst
# Wenn Beobachtungsart = "Tachymeter_Strecke" --> Übergabe Stabw_apriori_konst in Millimeter und Stabw_apriori_streckenprop in ppm

importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
importlib.reload(Berechnungen)

db_zugriff.set_genauigkeiten(1, "Tachymeter_Richtung", 0.15)
db_zugriff.set_genauigkeiten(1, "Tachymeter_Strecke", 0.8, 1)
db_zugriff.set_genauigkeiten(1, "Tachymeter_Zenitwinkel", 0.15)

In [ ]:
# Importieren der tachymetrischen Beobachtungen
importlib.reload(Import)
imp = Import.Import(pfad_datenbank)

pfad_datei_tachymeterbeobachtungen = r"Daten\campsnetz_beobachtungen_bereinigt.csv"

imp.import_beobachtungen_tachymeter(pfad_datei_tachymeterbeobachtungen, 1)

In [ ]:
# Jacobimatrix aufstellen
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

# Parameter des GRS80-ellipsoids (Bezugsellipsoid des ETRS89 / DREF 91 (2025)
# ToDo: Quelle mit möglichst genauen Parametern heraussuchen!
a = 6378137.0 #m
b = 63567552.314 #m

importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)

#db_zugriff.get_beobachtungen_id_standpunkt_zielpunkt("tachymeter_distanz")
Jacobimatrix_symbolisch = fm.jacobi_matrix_symbolisch()[0]
Jacobimatrix_symbolisch_liste_unbekannte = fm.jacobi_matrix_symbolisch()[1]
Jacobimatrix_symbolisch_liste_beobachtungsvektor = fm.jacobi_matrix_symbolisch()[2]

In [ ]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)

A_matrix_numerisch_iteration0 = fm.jacobi_matrix_zahlen_iteration_0(Jacobimatrix_symbolisch, "naeherung_us", Jacobimatrix_symbolisch_liste_unbekannte, Jacobimatrix_symbolisch_liste_beobachtungsvektor)

In [ ]:
importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)

beobachtungsvektor_numerisch = fm.beobachtungsvektor_numerisch(Jacobimatrix_symbolisch_liste_beobachtungsvektor)

In [ ]:
importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)

beobachtungsvektor_naeherung_symbolisch = fm.beobachtungsvektor_naeherung_symbolisch(Jacobimatrix_symbolisch_liste_beobachtungsvektor)

In [ ]:
importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)

beobachtungsvektor_naeherung_numerisch_iteration0 = fm.beobachtungsvektor_naeherung_numerisch_iteration0(Jacobimatrix_symbolisch_liste_beobachtungsvektor, beobachtungsvektor_naeherung_symbolisch)

In [ ]:
# Auftstellen der Qll-Matrix
importlib.reload(Stochastisches_Modell)
stoch_modell = Stochastisches_Modell.StochastischesModell(A_matrix_numerisch_iteration0.rows)

Qll_matrix_symbolisch = stoch_modell.Qll_symbolisch(pfad_datenbank, Jacobimatrix_symbolisch_liste_beobachtungsvektor)
Qll_matrix_numerisch = stoch_modell.Qll_numerisch(pfad_datenbank, Qll_matrix_symbolisch,Jacobimatrix_symbolisch_liste_beobachtungsvektor)

In [ ]:
importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)

importlib.reload(Parameterschaetzung)
importlib.reload(Stochastisches_Modell)

importlib.reload(Netzqualität_Genauigkeit)
importlib.reload(Export)


stoch_modell = Stochastisches_Modell.StochastischesModell(A_matrix_numerisch_iteration0.rows)

dx = Parameterschaetzung.ausgleichung_global(A_matrix_numerisch_iteration0, fm.berechnung_dl(beobachtungsvektor_numerisch, beobachtungsvektor_naeherung_numerisch_iteration0), stoch_modell)[1]

In [ ]:
# Von Fabian

importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)
importlib.reload(Export)
importlib.reload(Datenbank)

unbekanntenvektor_symbolisch = (fm.unbekanntenvektor_symbolisch(Jacobimatrix_symbolisch_liste_unbekannte))
unbekanntenvektor_numerisch_iteration0 = fm.unbekanntenvektor_numerisch(Jacobimatrix_symbolisch_liste_unbekannte, unbekanntenvektor_symbolisch)
print(unbekanntenvektor_numerisch_iteration0)
print("-----")
unbekanntenvektor_numerisch = fm.unbekanntenvektor_numerisch(Jacobimatrix_symbolisch_liste_unbekannte, unbekanntenvektor_symbolisch, dx, unbekanntenvektor_numerisch_iteration0)
print(unbekanntenvektor_numerisch)